In [2]:
import altair as alt
import pandas as pd
import warnings

interval = alt.selection_interval(encodings=['x'])

warnings.simplefilter(action='ignore', category=FutureWarning)
df = pd.read_csv("/homes/adrian/mdr_mtb-master/results/ABres/10_S4/DepthProfile_10_S4.csv", header = 0, sep = ',')
plt_df = df.loc[df["Gene"] == "embB" ]
print(plt_df)
depth = alt.Chart(plt_df).mark_bar().encode(
    x="Position:Q",
    y="Depth:Q",
    tooltip=["Mutation:Q","Resistance:Q"],
    color="Mutation"
).properties(width=800,height=400,title="10_S1_embB_depth").add_selection(
    interval
)

depth

      Gene  Position  Depth Mutation Antibiotic
0     embB   4246514      0        -          -
1     embB   4246515      0        -          -
2     embB   4246516      0        -          -
3     embB   4246517      0        -          -
4     embB   4246518      0        -          -
...    ...       ...    ...      ...        ...
3292  embB   4249806      0        -          -
3293  embB   4249807      0        -          -
3294  embB   4249808      0        -          -
3295  embB   4249809      0        -          -
3296  embB   4249810      0        -          -

[3297 rows x 5 columns]


alt.Chart(...)

In [1]:
import altair as alt
import pandas as pd
import warnings

alt.data_transformers.disable_max_rows()

interval = alt.selection_interval(encodings=['x'])

warnings.simplefilter(action='ignore', category=FutureWarning)
df = pd.read_csv("/homes/adrian/mdr_mtb-master/results/ABres/10_S4/DepthProfile_10_S4.csv", header = 0, sep = ',')
df["Gene"]=df["Gene"].str.split('_').str[0]

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"'
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y="mean(Depth)",
    color = alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey"))
).properties(title="Mean Depth per locus",width = 800, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 350, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 350, height = 200)

df2 = pd.read_csv("/homes/adrian/mdr_mtb-master/results/ABres/10_S4/ABres_10_S4.csv", header = 0, sep = '\t')
df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(df2.shape[0]):
    lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
df2["Mutation"]=lsmut
df2["LocMutation"]=lslocmut


base2 = alt.Chart(df2).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=350,height=100)

res = (base2.mark_circle(size=1800,color="red") +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(df2).mark_bar().encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",axis=alt.Axis(title= "Read depth")),
    color = "Var_Qual",
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=350,height=100)


(res | qual) & barchart & (poschart | zoom_chart)

alt.VConcatChart(...)

In [32]:
import altair as alt
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

abresprofile = "/homes/adrian/mdr_mtb-master/results/ABres/10_S4/ABres_10_S4.csv"
depthprofile = "/homes/adrian/mdr_mtb-master/results/ABres/10_S4/DepthProfile_10_S4.csv"

df = pd.read_csv(depthprofile, header = 0, sep = ',')
df["Gene"]=df["Gene"].str.split('_').str[0]

df2 = pd.read_csv(abresprofile, header = 0, sep = '\t')
df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(df2.shape[0]):
    lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
df2["Mutation"]=lsmut
df2["LocMutation"]=lslocmut

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"',
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y("mean(Depth)",scale=alt.Scale(type="log")),
    color = alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey")),
    tooltip = alt.Tooltip(["mean(Depth)"],format='.2f')
).properties(title="Mean Depth per locus",width = 800, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 350, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 350, height = 200)

base2 = alt.Chart(df2).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=350,height=100)

res = (base2.mark_circle(size=1800,color="red") +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(df2).mark_bar(color="#1f77b4").encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=350,height=100)


plot = (res | qual) & barchart & (poschart | zoom_chart)
plot

alt.VConcatChart(...)

In [89]:
import altair as alt
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

abresprofile = "/homes/adrian/mdr_mtb-master/results/ABres/3_S3/ABres_3_S3.csv"
depthprofile = "/homes/adrian/mdr_mtb-master/results/ABres/3_S3/DepthProfile_3_S3.csv"

df = pd.read_csv(depthprofile, header = 0, sep = ',')
df["Gene"]=df["Gene"].str.split('_').str[0]

df2 = pd.read_csv(abresprofile, header = 0, sep = '\t')
df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
lsmut = []
lslocmut = []
for i in range(df2.shape[0]):
    lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
df2["Mutation"]=lsmut
df2["LocMutation"]=lslocmut

selector = alt.selection_single(empty="all", fields=["Gene"])
intervall_selector = alt.selection_interval(empty="all", encodings=['x'])

base = alt.Chart(df).transform_calculate(
    color = 'datum.Antibiotic !== "-" ? "red" : "lightgrey"',
)

base_selector = base.add_selection(selector)

barchart = base_selector.mark_bar().encode(
    x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y("mean(Depth)",scale=alt.Scale(type="log")),
    color = alt.condition(selector, alt.value("#1f77b4"), alt.value("lightgrey")),
    tooltip = alt.Tooltip(["mean(Depth)"],format='.2f')
).properties(title="Mean Depth per locus",width = 780, height = 200)

poschart = base_selector.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
).transform_filter(selector).add_selection(intervall_selector).properties(title="Locus specific depth",width = 350, height = 200)

zoom_chart = base.mark_bar().encode(
    x="Position",
    y="Depth",
    color = alt.Color("color:N", scale = None),
    tooltip=["Mutation:N", "Antibiotic:N", "Depth"]
).transform_filter(intervall_selector).properties(title="Zoomed locus specific depth",width = 350, height = 200)

base2 = alt.Chart(df2).transform_calculate(
    color = 'datum.Resistance !== "-" ? "red" : "blue"',
).encode(
    x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
).properties(width=360,height=100)

res = (base2.mark_circle(size=1800).encode(color = alt.Color("color:N", scale = None)) +
       base2.mark_text(size=12).encode(text="Mut_gene") +
       base2.mark_text(dy=28,size=7).encode(text="Mutation"))

qual = alt.Chart(df2).mark_bar(color="#1f77b4").encode(
    x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
    y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
    tooltip = ["Var_Qual","Read_depth"]
).properties(width=360,height=100)


plot = alt.vconcat((res | qual), barchart, (poschart | zoom_chart),title=alt.TitleParams(
    text="Resistance plot",anchor="middle",fontWeight="bold",fontSize=20))
plot

alt.VConcatChart(...)

In [40]:
import pandas as pd

depthsum = "/homes/adrian/mdr_mtb-master/results/qc/samtools_depth/10_S4/10_S4_coverage_summary.txt"
df = pd.read_csv(depthsum, header= 0, sep = '\t')
df["#rname"]=df["#rname"].str.split('_').str[0]
df["startpos"]=df["endpos"]-df["startpos"]+1
df=df.drop(["endpos"],axis=1)
df=df.rename(columns={"#rname":"locus","startpos":"numpos"})
df

locus  numpos  numreads  covbases  coverage  meandepth  meanbaseq  \
0     embB    3297     18905       878   26.6303    821.151       35.1   
1     gidB     675     10717       675  100.0000   2139.150       36.0   
2     gyrA    2517     40345       422   16.7660   2292.960       36.0   
3     gyrB    2028     53574       685   33.7771   3807.950       35.8   
4     inhA     810     60374       634   78.2716  10835.500       36.1   
5     rplC     654     36689       375   57.3394   7812.280       35.2   
6     rpoB    3519    233806      1117   31.7420   9598.210       36.2   
7     rpsL     375     57509       375  100.0000  20710.200       36.5   
8      rrl    3138      7265       733   23.3588    333.108       35.8   
9      rrs    1537      3912      1537  100.0000    362.126       36.6   
10  rv0678     498     21352       498  100.0000   5826.650       35.0   
11    tlyA     807      3022       807  100.0000    482.581       34.7   
12     alr    1227         0         0    0.0000      0.000        0.0   
13    panD     420         0         0    0.0000      0.000        0.0   
14    drrA     996         0         0    0.0000      0.000        0.0   
15    folC    1464         0         0    0.0000      0.000        0.0   
16    embC    3285         0         0    0.0000      0.000        0.0   
17    embR    1167         0         0    0.0000      0.000        0.0   
18    ribD     777         0         0    0.0000      0.000        0.0   
19   fabG1     967     50546       475   49.1210   7481.250       35.9   
20    ahpC     768     47526       587   76.4323   8643.580       34.8   
21    embA    3400         0         0    0.0000      0.000        0.0   
22     eis    1328    244358       300   22.5904  22432.700       35.5   
23    ethA    1544     18087      1502   97.2798   1284.240       36.0   
24    katG    2330     13668       752   32.2747    847.579       35.9   
25    pncA     668     34705       637   95.3593   7484.280       35.7   

    meanmapq  
0       60.0  
1       60.0  
2       60.0  
3       59.9  
4       60.0  
5       60.0  
6       60.0  
7       60.0  
8       59.9  
9       60.0  
10      60.0  
11      60.0  
12       0.0  
13       0.0  
14       0.0  
15       0.0  
16       0.0  
17       0.0  
18       0.0  
19      60.0  
20      60.0  
21       0.0  
22      60.0  
23      60.0  
24      60.0  
25      60.0

In [51]:
import pandas as pd

depthsum1 = "/homes/adrian/mdr_mtb-master/results/10/qc/samtools_depth/1_S1/1_S1_coverage_summary.txt"
depthsum2 = "/homes/adrian/mdr_mtb-master/results/60/qc/samtools_depth/1_S1/1_S1_coverage_summary.txt"

df = pd.read_csv(depthsum1, header= 0, sep = '\t')
df["#rname"]=df["#rname"].str.split('_').str[0]
df["startpos"]=df["endpos"]-df["startpos"]+1
df=df.drop(["endpos"],axis=1)
df=df.rename(columns={"#rname":"locus","startpos":"numpos"})
df.insert(1, 'read_reduction', 10)

df2 = pd.read_csv(depthsum1, header= 0, sep = '\t')
df2["#rname"]=df2["#rname"].str.split('_').str[0]
df2["startpos"]=df2["endpos"]-df2["startpos"]+1
df2=df2.drop(["endpos"],axis=1)
df2=df2.rename(columns={"#rname":"locus","startpos":"numpos"})
df2.insert(1, 'read_reduction', 60)
frames = [df,df2]

df3 = pd.concat(frames).sort_values(['locus','read_reduction'])
df3

locus  read_reduction  numpos  numreads  covbases  coverage   meandepth  \
20    ahpC              10     768     23386       587   76.4323   4231.4800   
20    ahpC              60     768     23386       587   76.4323   4231.4800   
12     alr              10    1227         0         0    0.0000      0.0000   
12     alr              60    1227         0         0    0.0000      0.0000   
14    drrA              10     996         0         0    0.0000      0.0000   
14    drrA              60     996         0         0    0.0000      0.0000   
22     eis              10    1328    243532       299   22.5151  22288.7000   
22     eis              60    1328    243532       299   22.5151  22288.7000   
21    embA              10    3400         0         0    0.0000      0.0000   
21    embA              60    3400         0         0    0.0000      0.0000   
0     embB              10    3297      2991       724   21.9594    128.9390   
0     embB              60    3297      2991       724   21.9594    128.9390   
16    embC              10    3285         0         0    0.0000      0.0000   
16    embC              60    3285         0         0    0.0000      0.0000   
17    embR              10    1167         0         0    0.0000      0.0000   
17    embR              60    1167         0         0    0.0000      0.0000   
23    ethA              10    1544      9228      1501   97.2150    499.0240   
23    ethA              60    1544      9228      1501   97.2150    499.0240   
19   fabG1              10     967     32894       469   48.5005   4845.9900   
19   fabG1              60     967     32894       469   48.5005   4845.9900   
15    folC              10    1464         0         0    0.0000      0.0000   
15    folC              60    1464         0         0    0.0000      0.0000   
1     gidB              10     675      1241       675  100.0000    247.2900   
1     gidB              60     675      1241       675  100.0000    247.2900   
2     gyrA              10    2517     26902       419   16.6468   1520.1900   
2     gyrA              60    2517     26902       419   16.6468   1520.1900   
3     gyrB              10    2028     12297       688   33.9250    869.6810   
3     gyrB              60    2028     12297       688   33.9250    869.6810   
4     inhA              10     810     21569       646   79.7531   3829.4500   
4     inhA              60     810     21569       646   79.7531   3829.4500   
24    katG              10    2330      2612       750   32.1888    159.8850   
24    katG              60    2330      2612       750   32.1888    159.8850   
13    panD              10     420         0         0    0.0000      0.0000   
13    panD              60     420         0         0    0.0000      0.0000   
25    pncA              10     668     10677       637   95.3593   2296.6400   
25    pncA              60     668     10677       637   95.3593   2296.6400   
18    ribD              10     777         0         0    0.0000      0.0000   
18    ribD              60     777         0         0    0.0000      0.0000   
5     rplC              10     654     27072       373   57.0336   5728.5700   
5     rplC              60     654     27072       373   57.0336   5728.5700   
6     rpoB              10    3519    136474      1008   28.6445   5489.7600   
6     rpoB              60    3519    136474      1008   28.6445   5489.7600   
7     rpsL              10     375     35036       375  100.0000  12570.9000   
7     rpsL              60     375     35036       375  100.0000  12570.9000   
8      rrl              10    3138      1678       882   28.1071     76.1409   
8      rrl              60    3138      1678       882   28.1071     76.1409   
9      rrs              10    1537      1222      1537  100.0000    114.4900   
9      rrs              60    1537      1222      1537  100.0000    114.4900   
10  rv0678              10     498      6817       498  100.0000   1849.8800   
10  r

In [92]:
import altair as alt
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

abresprofile1 = "/homes/adrian/mdr_mtb-master/results/10/ABres/3_S3/ABres_3_S3.csv"
depthprofile1 = "/homes/adrian/mdr_mtb-master/results/10/ABres/3_S3/DepthProfile_3_S3.csv"
abresprofile2 = "/homes/adrian/mdr_mtb-master/results/60/ABres/3_S3/ABres_3_S3.csv"
depthprofile2 = "/homes/adrian/mdr_mtb-master/results/60/ABres/3_S3/DepthProfile_3_S3.csv"

sminput1=[abresprofile1,abresprofile2]
sminput2=[depthprofile1,depthprofile2]

param = ["10","60"]

i=0
lis = []
for depthprofile,abresprofile,par in zip(sminput2,sminput1,param):
    df = pd.read_csv(depthprofile, header = 0, sep = ',')
    df["Gene"]=df["Gene"].str.split('_').str[0]

    df2 = pd.read_csv(abresprofile, header = 0, sep = '\t')
    df2["Mut_gene"]=df2["Mut_gene"].str.split('_').str[0]
    lsmut = []
    lslocmut = []
    for i in range(df2.shape[0]):
        lsmut.append(df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
        lslocmut.append(df2.loc[i]["Mut_gene"]+"_"+df2.loc[i]["Ref_Codon"]+str(df2.loc[i]["Codon_num"])+df2.loc[i]["Alt_Codon"])
    df2["Mutation"]=lsmut
    df2["LocMutation"]=lslocmut
    barchart = alt.Chart(df).mark_bar(color = "#1f77b4").encode(
        x=alt.X("Gene:O", title = None,axis=alt.Axis(labelAngle=-45)),
        y=alt.Y("mean(Depth)",scale=alt.Scale(type="log")),
        tooltip = alt.Tooltip(["mean(Depth)"],format='.2f')
    ).properties(title="Mean Depth per locus",width = 780, height = 200)

    base2 = alt.Chart(df2).transform_calculate(
        color = 'datum.Resistance !== "-" ? "red" : "blue"',
    ).encode(
        x=alt.X("Resistance",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,labelFontSize=10,tickWidth=0,domain=False)),
    ).properties(width=360,height=100)

    res = (base2.mark_circle(size=1800).encode(color = alt.Color("color:N", scale = None)) +
           base2.mark_text(size=12).encode(text="Mut_gene") +
           base2.mark_text(dy=28,size=7).encode(text="Mutation"))

    qual = alt.Chart(df2).mark_bar(color="#1f77b4").encode(
        x=alt.X("LocMutation",sort=["Resistance"],axis=alt.Axis(orient="top",labelAngle=35,title="Mutation specifics",tickWidth=0)),
        y=alt.Y("Read_depth",scale=alt.Scale(type="log"),axis=alt.Axis(title= "Read depth")),
        tooltip = ["Var_Qual","Read_depth"]
    ).properties(width=360,height=100)
    lis.append(alt.vconcat((res | qual), barchart,title=alt.TitleParams(
        text="Resistance plot -"+par+"%",anchor="middle",fontWeight="bold",fontSize=20)))
a=alt.hconcat(*lis)
a.save(snakemake.output[0])

alt.HConcatChart(...)